In [1]:
from nltk.corpus import wordnet as wn

In [2]:
# syn = wn.synset_from_pos_and_offset('n', 2108089)
# syn = wn.synset_from_pos_and_offset('n', 2128385)
syn = wn.synset('domestic_cat.n.01')
print(syn)
syn.hypernym_paths()

Synset('domestic_cat.n.01')


[[Synset('entity.n.01'),
  Synset('physical_entity.n.01'),
  Synset('object.n.01'),
  Synset('whole.n.02'),
  Synset('living_thing.n.01'),
  Synset('organism.n.01'),
  Synset('animal.n.01'),
  Synset('chordate.n.01'),
  Synset('vertebrate.n.01'),
  Synset('mammal.n.01'),
  Synset('placental.n.01'),
  Synset('carnivore.n.01'),
  Synset('feline.n.01'),
  Synset('cat.n.01'),
  Synset('domestic_cat.n.01')],
 [Synset('entity.n.01'),
  Synset('physical_entity.n.01'),
  Synset('object.n.01'),
  Synset('whole.n.02'),
  Synset('living_thing.n.01'),
  Synset('organism.n.01'),
  Synset('animal.n.01'),
  Synset('domestic_animal.n.01'),
  Synset('domestic_cat.n.01')]]

In [3]:
f = open("synset_words.txt", "r")
labels = f.readlines()
f.close()
labels = [label.split()[0] for label in labels]
labels = [[label[0], label[1:]] for label in labels]

In [4]:
# Check how many labels have more than one hypernym.

def find_all_hypernyms(synset):
    hypernyms = synset.hypernyms()
    if len(hypernyms) > 1:
        print(synset)
        print(hypernyms)
    if len(hypernyms) == 0:
        return []
    else:
        return hypernyms + list(sum(map(find_all_hypernyms, hypernyms),[]))

for label in labels:
    synset = wn.synset_from_pos_and_offset(label[0], int(label[1]))
    find_all_hypernyms(synset)

Synset('game_bird.n.01')
[Synset('gallinaceous_bird.n.01'), Synset('game.n.04')]
Synset('game_bird.n.01')
[Synset('gallinaceous_bird.n.01'), Synset('game.n.04')]
Synset('game_bird.n.01')
[Synset('gallinaceous_bird.n.01'), Synset('game.n.04')]
Synset('game_bird.n.01')
[Synset('gallinaceous_bird.n.01'), Synset('game.n.04')]
Synset('game_bird.n.01')
[Synset('gallinaceous_bird.n.01'), Synset('game.n.04')]
Synset('game_bird.n.01')
[Synset('gallinaceous_bird.n.01'), Synset('game.n.04')]
Synset('game_bird.n.01')
[Synset('gallinaceous_bird.n.01'), Synset('game.n.04')]
Synset('dog.n.01')
[Synset('canine.n.02'), Synset('domestic_animal.n.01')]
Synset('dog.n.01')
[Synset('canine.n.02'), Synset('domestic_animal.n.01')]
Synset('dog.n.01')
[Synset('canine.n.02'), Synset('domestic_animal.n.01')]
Synset('dog.n.01')
[Synset('canine.n.02'), Synset('domestic_animal.n.01')]
Synset('dog.n.01')
[Synset('canine.n.02'), Synset('domestic_animal.n.01')]
Synset('dog.n.01')
[Synset('canine.n.02'), Synset('domesti

In [5]:
# build semantice tree

import networkx as nx

graph = nx.DiGraph()

for label in labels:
    to_add = wn.synset_from_pos_and_offset(label[0], int(label[1]))
    graph.add_node(to_add)
    minimum_depth_to_add = 1000
    minimum_depth_to_existing = 1000
    minimun_depth_node = None
    minimun_depth_node_in_graph = None
    hypernym_paths = to_add.hypernym_paths()
    hypernym_paths = [hypernym_paths[0]] # select the first path
    for l in hypernym_paths:
        l.reverse()
    # find the lowest common hypernym
    for node in graph.nodes:
        if node == to_add:
            continue
        lowest_common_hypernyms = to_add.lowest_common_hypernyms(node)[0]
        depth = min([l.index(lowest_common_hypernyms) if lowest_common_hypernyms in l else 10000 for l in hypernym_paths])
        if depth < minimum_depth_to_add:
            minimum_depth_to_add = depth
            node_hypernym_paths = node.hypernym_paths()
            node_hypernym_paths = [node_hypernym_paths[0]] # select the first path
            for l in node_hypernym_paths:
                l.reverse()
            minimum_depth_to_existing = min([l.index(lowest_common_hypernyms) if lowest_common_hypernyms in l else 10000 for l in node_hypernym_paths])
            minimun_depth_node = lowest_common_hypernyms
            minimun_depth_node_in_graph = node
        elif depth == minimum_depth_to_add:
            node_hypernym_paths = node.hypernym_paths()
            node_hypernym_paths = [node_hypernym_paths[0]] # select the first path
            for l in node_hypernym_paths:
                l.reverse()
            depth_to_existing = min([l.index(lowest_common_hypernyms) if lowest_common_hypernyms in l else 10000 for l in node_hypernym_paths])
            if depth_to_existing < minimum_depth_to_existing:
                minimum_depth_to_existing = depth_to_existing
                minimun_depth_node = lowest_common_hypernyms
                minimun_depth_node_in_graph = node
    # if minimun_depth_node is in the graph, simplily connect it to the new node:
    # if minimun_depth_node is not in the graph, add it to the graph and rearrange the edges
    if minimun_depth_node not in graph.nodes and minimun_depth_node is not None:
        graph.add_node(minimun_depth_node)
        # if minimun_depth_node.name() == 'domestic_cat.n.01':
        #     print('domestic_cat.n.01')
        # if minimun_depth_node.name() == 'feline.n.01':
        #     print('feline.n.01')
        # if minimun_depth_node.name() == 'vertebrate.n.01':
        #     print('vertebrate.n.01')
        # if minimun_depth_node.name() == 'placental.n.01':
        #     print('placental.n.01')
        # if minimun_depth_node.name() == 'mammal.n.01':
        #     print('mammal.n.01')
        for edge in graph.edges:
            if edge[1] == minimun_depth_node_in_graph:
                graph.remove_edge(edge[0], edge[1])
                graph.add_edge(edge[0], minimun_depth_node)
                # edge[1]=minimun_depth_node
                graph.add_edge(minimun_depth_node, minimun_depth_node_in_graph)
                break 
        graph.add_edge(minimun_depth_node, minimun_depth_node_in_graph)
    if minimun_depth_node is not None:
        graph.add_edge(minimun_depth_node, to_add)

nx.write_gexf(graph, "semantic_tree.gexf")

TypeError: cannot pickle '_thread.RLock' object

In [7]:
# import matplotlib.pyplot as plt
# plt.figure()
# nx.draw(graph)

import matplotlib.pyplot as plt
import networkx as nx

labeldict = {}
for synset in graph.nodes():
    labeldict[synset] = synset.name().split('.')[0]

plt.figure(figsize=(120, 50))
pos = nx.nx_agraph.graphviz_layout(graph, prog="dot")
nx.draw(graph, pos, node_size=2, alpha = 0.3, with_labels=False)

text = nx.draw_networkx_labels(graph, pos, labels=labeldict, font_size=15)
for _, t in text.items():
    t.set_rotation('vertical') 
    
plt.savefig('semantic_tree.png')
# plt.show()


In [7]:
len(list(graph.nodes))

1380